In [2]:
# Import Librarys that will be used

In [2]:
import numpy as np
import pandas as pd
import requests
from bs4 import BeautifulSoup
#!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim4
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans

#!pip install folium
import folium # map rendering library

Wikipedia page Scraping

In [3]:
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
page = requests.get(url).text
content = BeautifulSoup(page,"html.parser")
neigh = []
postcode = []
borough = []
x = content.body.table.find_all('tr')[1:]
for item in x:
    postcode.append(item.find_all('td')[0].text)
    borough.append(item.find_all('td')[1].text)
    try:
        neigh.append(item.find_all('td')[2].a.text)
    except:
        neigh.append('Not assigned')

df = pd.DataFrame({'Postcode':postcode,'Borough':borough,'Neighborhood':neigh})

Droping Not assigned Values

In [4]:
df.drop(df[df['Borough']== 'Not assigned'].index,inplace = True)

Assigning the same borough to Not assigned neighborhood

In [5]:
for i,row in df.iterrows():
    if row['Neighborhood'] == 'Not assigned':
        row['Neighborhood'] = row['Borough']

Grouping same NeighborHood to Postcode Values

In [6]:
df['Neighborhood'] = df['Neighborhood'].groupby(df['Postcode']).transform(lambda x : ','.join(x))

Remove Duplicates and reset the dataframe index

In [7]:
df.drop_duplicates(subset = 'Postcode',keep = 'first', inplace = True)
df.reset_index(drop=True, inplace=True)
df.head()

Postcode           Borough                     Neighborhood
0      M3A        North York                        Parkwoods
1      M4A        North York                 Victoria Village
2      M5A  Downtown Toronto         Harbourfront,Regent Park
3      M6A        North York  Lawrence Heights,Lawrence Manor
4      M7A      Queen's Park                     Queen's Park

Get longetude and latitude

In [8]:
geodata = pd.read_csv('http://cocl.us/Geospatial_data')

In [9]:
geodata.columns = ['Postcode','Latitude','Longitude']
geodata.head()

Postcode   Latitude  Longitude
0      M1B  43.806686 -79.194353
1      M1C  43.784535 -79.160497
2      M1E  43.763573 -79.188711
3      M1G  43.770992 -79.216917
4      M1H  43.773136 -79.239476

In [10]:
lat = []
long = []

for i,row in df.iterrows():
    pc = row['Postcode']
    for j,r in geodata.iterrows():
        if pc == r['Postcode']:
            lat.append(r['Latitude'])
            long.append(r['Longitude'])
            break
df['Latitude'] = lat
df['Longitude'] = long
df.head()

Postcode           Borough                     Neighborhood   Latitude  \
0      M3A        North York                        Parkwoods  43.753259   
1      M4A        North York                 Victoria Village  43.725882   
2      M5A  Downtown Toronto         Harbourfront,Regent Park  43.654260   
3      M6A        North York  Lawrence Heights,Lawrence Manor  43.718518   
4      M7A      Queen's Park                     Queen's Park  43.662301   

   Longitude  
0 -79.329656  
1 -79.315572  
2 -79.360636  
3 -79.464763  
4 -79.389494

Get longtiude and latitude of  Toronto, Ontario

In [31]:
from geopy.exc import GeocoderTimedOut
address = 'Toronto, Ontario'
try:
    geolocator = Nominatim(user_agent="trnto_explorer")
    location = geolocator.geocode(address, timeout=None)
    latitude = location.latitude
    longitude = location.longitude
    print('The geograpical coordinate of Toronto, Ontario City are {}, {}.'.format(latitude, longitude))
except GeocoderTimedOut as e:
     print("Error: geocode failed on input %s with message %s"%(address, e.message))

C:\Users\khairy\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: DeprecationWarning: `timeout=None` has been passed to a geocoder call. Using default geocoder timeout. In geopy 2.0 the behavior will be different: None will mean "no timeout" instead of "default geocoder timeout". Pass geopy.geocoders.base.DEFAULT_SENTINEL instead of None to get rid of this warning.
  """


The geograpical coordinate of Toronto, Ontario City are 43.653963, -79.387207.


Create map for toronto and it's neighborhoods

In [66]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood,postcode in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood'],df['Postcode']):
    label = '{}, {} ,{}'.format(neighborhood, borough,postcode)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

Define forsquare

In [33]:
CLIENT_ID = 'ULMCH3VB2W5X4XB5ZC2FPZIF1BCWLSBNAMJU30H1BQGOC040' # your Foursquare ID
CLIENT_SECRET = 'P5HVEJDG12UPKLTJFE5IMQ0Z5EAIQHVZQPLHJVZOCJYTXW43' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: ULMCH3VB2W5X4XB5ZC2FPZIF1BCWLSBNAMJU30H1BQGOC040
CLIENT_SECRET:P5HVEJDG12UPKLTJFE5IMQ0Z5EAIQHVZQPLHJVZOCJYTXW43


Get each category type for each neighborhood

In [34]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Get 100 venius foreach neighborhood with radius 500

In [35]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            100)
            
        # make the GET request
        try:
            results = requests.get(url).json()["response"]['groups'][0]['items']

            # return only relevant information for each nearby venue
            venues_list.append([(
                name, 
                lat, 
                lng, 
                v['venue']['name'], 
                v['venue']['location']['lat'], 
                v['venue']['location']['lng'],  
                v['venue']['categories'][0]['name']) for v in results])
        except:
            continue

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [37]:
toronto_venues = getNearbyVenues(names=df['Neighborhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront,Regent Park
Lawrence Heights,Lawrence Manor
Queen's Park
Islington Avenue
Rouge,Malvern
North York
Woodbine Gardens,Parkview Hill
Downtown Toronto,Downtown Toronto
North York
Etobicoke,Islington,Etobicoke,Princess Gardens,West Deane Park
Highland Creek,Rouge Hill,Port Union
Flemingdon Park,North York
Woodbine Heights
St. James Town
Humewood-Cedarvale
Etobicoke,Etobicoke,Markland Wood,Etobicoke
Scarborough,Morningside,West Hill
The Beaches
Berczy Park
York
Woburn
Leaside
Downtown Toronto
Downtown Toronto
Scarborough
Hillcrest Village
Bathurst Manor,North York,Wilson Heights
Thorncliffe Park
Downtown Toronto,Downtown Toronto,Downtown Toronto
Dovercourt Village,West Toronto
Scarborough Village
North York,Henry Farm,North York
Northwood Park,York University
East Toronto
Downtown Toronto,Toronto Islands,Union Station
Little Portugal,Trinity
Scarborough,Ionview,Kennedy Park
Bayview Village
CFB Toronto,North York
East Toronto,Riverdale
Design Exchange,T

In [38]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2         Parkwoods              43.753259              -79.329656   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                        Venue  Venue Latitude  Venue Longitude  \
0             Brookbanks Park       43.751976       -79.332140   
1               Variety Store       43.751974       -79.333114   
2  TTC stop - 44 Valley Woods       43.755402       -79.333741   
3      Victoria Village Arena       43.723481       -79.315635   
4                 Tim Hortons       43.725517       -79.313103   

      Venue Category  
0               Park  
1  Food & Drink Shop  
2           Bus Stop  
3       Hockey Arena  
4        Coffee Shop

In [39]:
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant      ...        Trail  Train Station  \
0                 0                    0      ...            0              0   
1                 0                    0      ...            0              0   
2                 0                    0      ...            0              0   
3                 0                    0      ...            0              0   
4                 0                    0      ...            0              0   

   Vegetarian / Vegan Restaurant  Video Game Store  Video Store  \
0                              0                 0            0   
1                              0                 0            0   
2                              0                 0            0   
3                              0                 0            0   
4                              0                 0            0   

   Vietnamese Restaurant  Warehouse Store  Wine Bar  Wings Joint  \
0                      0                0         0            0   
1                      0                0         0            0   
2                      0                0         0            0   
3                      0                0         0            0   
4                      0                0         0            0   

   Women's Store  
0              0  
1              0  
2              0  
3              0  
4              0  

[5 rows x 270 columns]

In [40]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped.head()

Neighborhood  Yoga Studio  \
0                                         Agincourt          0.0   
1  Agincourt North,Scarborough,Milliken,Scarborough          0.0   
2                             Alderwood,Long Branch          0.0   
3          Bathurst Manor,North York,Wilson Heights          0.0   
4                                   Bayview Village          0.0   

   Accessories Store  Afghan Restaurant  Airport  Airport Food Court  \
0                0.0                0.0      0.0                 0.0   
1                0.0                0.0      0.0                 0.0   
2                0.0                0.0      0.0                 0.0   
3                0.0                0.0      0.0                 0.0   
4                0.0                0.0      0.0                 0.0   

   Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0           0.0             0.0              0.0               0.0   
1           0.0             0.0              0.0               0.0   
2           0.0             0.0              0.0               0.0   
3           0.0             0.0              0.0               0.0   
4           0.0             0.0              0.0               0.0   

       ...        Trail  Train Station  Vegetarian / Vegan Restaurant  \
0      ...          0.0            0.0                            0.0   
1      ...          0.0            0.0                            0.0   
2      ...          0.0            0.0                            0.0   
3      ...          0.0            0.0                            0.0   
4      ...          0.0            0.0                            0.0   

   Video Game Store  Video Store  Vietnamese Restaurant  Warehouse Store  \
0               0.0     0.000000                    0.0              0.0   
1               0.0     0.000000                    0.0              0.0   
2               0.0     0.000000                    0.0              0.0   
3               0.0     0.055556                    0.0              0.0   
4               0.0     0.000000                    0.0              0.0   

   Wine Bar  Wings Joint  Women's Store  
0       0.0          0.0            0.0  
1       0.0          0.0            0.0  
2       0.0          0.0            0.0  
3       0.0          0.0            0.0  
4       0.0          0.0            0.0  

[5 rows x 270 columns]

Extract Café in toronto

In [41]:
toronto_cafe = pd.DataFrame()
toronto_cafe['cafe'] = toronto_grouped.loc[:,'Café']
toronto_cafe['Neighborhood'] = toronto_grouped.loc[:,'Neighborhood']
toronto_cafe.head()

cafe                                      Neighborhood
0  0.00                                         Agincourt
1  0.00  Agincourt North,Scarborough,Milliken,Scarborough
2  0.00                             Alderwood,Long Branch
3  0.00          Bathurst Manor,North York,Wilson Heights
4  0.25                                   Bayview Village

Start Clustring

In [42]:
kclusters = 3

toronto_cafe_clustering = toronto_cafe.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_cafe_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([2, 2, 2, 2, 1, 0, 1, 2, 2, 0, 0, 0, 2, 2, 2, 0, 2, 0, 2, 0, 2, 2,
       0, 2, 0, 0, 1, 0, 2, 2, 2, 2, 2, 0, 0, 2, 0, 2, 2, 0, 2, 2, 2, 2,
       2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 0, 2, 2, 2, 2, 2, 2, 2, 0, 2, 2, 2,
       2, 2, 0, 1, 2, 2, 2, 2, 0, 2, 2, 2, 2, 2, 2, 2, 2])

Reconstruct Data Frame to contain Neighborhood longitude and latitude

In [87]:
#toronto_cafe_clustering.insert(0, 'Cluster Labels', kmeans.labels_)
#toronto_cafe_clustering.insert(0, 'Neighborhood', df['Neighborhood'])
toronto_merged = toronto_venues

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(toronto_cafe_clustering.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2         Parkwoods              43.753259              -79.329656   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                        Venue  Venue Latitude  Venue Longitude  \
0             Brookbanks Park       43.751976       -79.332140   
1               Variety Store       43.751974       -79.333114   
2  TTC stop - 44 Valley Woods       43.755402       -79.333741   
3      Victoria Village Arena       43.723481       -79.315635   
4                 Tim Hortons       43.725517       -79.313103   

      Venue Category  Cluster Labels  cafe  
0               Park             2.0   0.0  
1  Food & Drink Shop             2.0   0.0  
2           Bus Stop             2.0   0.0  
3       Hockey Arena             2.0   0.0  
4        Coffee Shop             2.0   0.0

Sort By Class label

In [98]:
toronto_merged.sort_values(["Cluster Labels"],ascending = False, inplace=True)
toronto_merged.reset_index(drop=True, inplace=True)
toronto_merged.head()


Neighborhood  Neighborhood Latitude  \
0                        Parkwoods              43.753259   
1  Commerce Court,Downtown Toronto              43.648198   
2  Commerce Court,Downtown Toronto              43.648198   
3  Commerce Court,Downtown Toronto              43.648198   
4  Commerce Court,Downtown Toronto              43.648198   

   Neighborhood Longitude                                Venue  \
0              -79.329656                      Brookbanks Park   
1              -79.379817                              Terroni   
2              -79.379817                     Pravda Vodka Bar   
3              -79.379817                Toronto Athletic Club   
4              -79.379817  Sony Centre for the Performing Arts   

   Venue Latitude  Venue Longitude      Venue Category  Cluster Labels  cafe  
0       43.751976       -79.332140                Park             2.0   0.0  
1       43.650927       -79.375602  Italian Restaurant             2.0   0.0  
2       43.648516       -79.374732        Cocktail Bar             2.0   0.0  
3       43.647360       -79.381177                 Gym             2.0   0.0  
4       43.646292       -79.376022        Concert Hall             2.0   0.0

Cluster labels Preprocessing

In [117]:
ind = np.array(toronto_merged[toronto_merged['Cluster Labels'].isnull()]['Cluster Labels'].index)
toronto_merged.loc[ind,'Cluster Labels'] = 0

In [118]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Neighborhood Latitude'], toronto_merged['Neighborhood Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
map_clusters

In [119]:
map_clusters.save('map.html')

# observation
It seems that if you get nearer to the center of the city you will get much cafe's but the areas far from the center are much fewer ones.SO,it's smart to open in places as Victoria Village or Etobicoke marked as cluster 2 as it will be less competition with other caafe's.